In [9]:
# !pip install pyLDAvis

In [1]:
from sklearn.datasets import fetch_20newsgroups

import gensim
import pyLDAvis.gensim
from gensim.utils import simple_preprocess
from gensim.parsing.preprocessing import STOPWORDS
from nltk.stem import WordNetLemmatizer, SnowballStemmer
from nltk.stem.porter import *
import numpy as np
np.random.seed(400)

In [2]:
data_train = fetch_20newsgroups(subset='train',shuffle=True,
                                random_state=42,
                               remove=('header','footer','quotes'))
data_test = fetch_20newsgroups(subset='test', shuffle=True,
                               random_state=42,
                              remove=('header','footer','quotes'))

In [3]:
set(data_train.target_names)
# set(data_test.target_names)
process_data = data_train.data

In [4]:
def lemmatize_stemming(text):
    stemmer = SnowballStemmer("english")
    return stemmer.stem(WordNetLemmatizer().lemmatize(text, pos='v'))

# Tokenize and lemmatize
def preprocess(text):
    result=[]
    for token in gensim.utils.simple_preprocess(text):
        # Give word . Return the fequency of word\n",
        # Exclude STOPWORD, everything very less then 3\n",
        if token not in gensim.parsing.preprocessing.STOPWORDS and len(token) > 3:
            result.append(lemmatize_stemming(token))
            
    return result

In [5]:
process_data[::3]

["From: lerxst@wam.umd.edu (where's my thing)\nSubject: WHAT car is this!?\nNntp-Posting-Host: rac3.wam.umd.edu\nOrganization: University of Maryland, College Park\nLines: 15\n\n I was wondering if anyone out there could enlighten me on this car I saw\nthe other day. It was a 2-door sports car, looked to be from the late 60s/\nearly 70s. It was called a Bricklin. The doors were really small. In addition,\nthe front bumper was separate from the rest of the body. This is \nall I know. If anyone can tellme a model name, engine specs, years\nof production, where this car is made, history, or whatever info you\nhave on this funky looking car, please e-mail.\n\nThanks,\n- IL\n   ---- brought to you by your neighborhood Lerxst ----\n\n\n\n\n",
 'From: jgreen@amber (Joe Green)\nSubject: Re: Weitek P9000 ?\nOrganization: Harris Computer Systems Division\nLines: 14\nDistribution: world\nNNTP-Posting-Host: amber.ssd.csd.harris.com\nX-Newsreader: TIN [version 1.1 PL9]\n\n\nDo you have Weitek\'s ad

In [19]:
print(preprocess(process_data[100]))

['tchen', 'magnus', 'ohio', 'state', 'tsung', 'chen', 'subject', 'softwar', 'forsal', 'lot', 'nntp', 'post', 'host', 'magnusug', 'magnus', 'ohio', 'state', 'organ', 'ohio', 'state', 'univers', 'post', 'friend', 'drop', 'mail', 'distribut', 'line', 'softwar', 'publish', 'superbas', 'window', 'readright', 'window', 'readright', 'unregist', 'zortech', 'compil', 'multiscop', 'window', 'debugg', 'whitewat', 'resourc', 'toolkit', 'librari', 'sourc', 'code', 'glockenspiel', 'imagesoft', 'commonview', 'window', 'applic', 'framework', 'borland', 'spontan', 'assembl', 'librari', 'sourc', 'code', 'microsoft', 'macro', 'assembl', 'microsoft', 'window', 'document', 'microsoft', 'foxpro', 'wordperfect', 'develop', 'toolkit', 'kedwel', 'softwar', 'databoss', 'code', 'generat', 'kedwel', 'installboss', 'instal', 'generat', 'liant', 'softwar', 'view', 'window', 'applic', 'framework', 'sourc', 'code', 'develop', 'toolkit', 'cbtree', 'window', 'librari', 'sourc', 'code', 'symantec', 'timelin', 'window', 

In [20]:
print(gensim.utils.simple_preprocess(process_data[100]))

['from', 'tchen', 'magnus', 'acs', 'ohio', 'state', 'edu', 'tsung', 'kun', 'chen', 'subject', 'software', 'forsale', 'lots', 'nntp', 'posting', 'host', 'magnusug', 'magnus', 'acs', 'ohio', 'state', 'edu', 'organization', 'the', 'ohio', 'state', 'university', 'this', 'is', 'post', 'for', 'my', 'friend', 'you', 'can', 'either', 'call', 'him', 'lee', 'or', 'drop', 'me', 'mail', 'distribution', 'usa', 'lines', 'software', 'publishing', 'superbase', 'windows', 'ocr', 'system', 'readright', 'for', 'windows', 'ocr', 'system', 'readright', 'for', 'dos', 'unregistered', 'zortech', 'bit', 'compiler', 'with', 'multiscope', 'windows', 'debugger', 'whitewater', 'resource', 'toolkit', 'library', 'source', 'code', 'glockenspiel', 'imagesoft', 'commonview', 'windows', 'applications', 'framework', 'for', 'borland', 'spontaneous', 'assembly', 'library', 'with', 'source', 'code', 'microsoft', 'macro', 'assembly', 'microsoft', 'windows', 'sdk', 'documentation', 'microsoft', 'foxpro', 'wordperfect', 'devel

In [6]:
processed_docs = []

for doc in data_train.data:
    processed_docs.append(preprocess(doc))

In [8]:
# Push to dictionary
dictionary = gensim.corpora.Dictionary(processed_docs)

In [9]:
# "# I dont want words no_below, no_above
dictionary.filter_extremes(no_below=10, no_above=0.2,keep_n=1000)

In [10]:
# "# Bag of words
bow_corpus = [dictionary.doc2bow(doc) for doc in processed_docs]

In [ ]:
# Fit LDA model\n",
# num_topic [dont know] sothat pick a proper number,
lda_model = gensim.models.LdaMulticore(bow_corpus,
                                       num_topics=8,
                                      id2word=dictionary,
                                     passes=10, workers=2)

/home/shayne/Anaconda3/envs/caps_env/lib/python3.6/site-packages/gensim/models/ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
/home/shayne/Anaconda3/envs/caps_env/lib/python3.6/site-packages/gensim/models/ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
/home/shayne/Anaconda3/envs/caps_env/lib/python3.6/site-packages/gensim/models/ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instea

/home/shayne/Anaconda3/envs/caps_env/lib/python3.6/site-packages/gensim/models/ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
/home/shayne/Anaconda3/envs/caps_env/lib/python3.6/site-packages/gensim/models/ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
/home/shayne/Anaconda3/envs/caps_env/lib/python3.6/site-packages/gensim/models/ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instea

/home/shayne/Anaconda3/envs/caps_env/lib/python3.6/site-packages/gensim/models/ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
/home/shayne/Anaconda3/envs/caps_env/lib/python3.6/site-packages/gensim/models/ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
/home/shayne/Anaconda3/envs/caps_env/lib/python3.6/site-packages/gensim/models/ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instea

/home/shayne/Anaconda3/envs/caps_env/lib/python3.6/site-packages/gensim/models/ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
/home/shayne/Anaconda3/envs/caps_env/lib/python3.6/site-packages/gensim/models/ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
/home/shayne/Anaconda3/envs/caps_env/lib/python3.6/site-packages/gensim/models/ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instea

/home/shayne/Anaconda3/envs/caps_env/lib/python3.6/site-packages/gensim/models/ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
/home/shayne/Anaconda3/envs/caps_env/lib/python3.6/site-packages/gensim/models/ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
/home/shayne/Anaconda3/envs/caps_env/lib/python3.6/site-packages/gensim/models/ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instea

...

/home/shayne/Anaconda3/envs/caps_env/lib/python3.6/site-packages/gensim/models/ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
/home/shayne/Anaconda3/envs/caps_env/lib/python3.6/site-packages/gensim/models/ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
/home/shayne/Anaconda3/envs/caps_env/lib/python3.6/site-packages/gensim/models/ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instea

/home/shayne/Anaconda3/envs/caps_env/lib/python3.6/site-packages/gensim/models/ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
/home/shayne/Anaconda3/envs/caps_env/lib/python3.6/site-packages/gensim/models/ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
/home/shayne/Anaconda3/envs/caps_env/lib/python3.6/site-packages/gensim/models/ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instea

/home/shayne/Anaconda3/envs/caps_env/lib/python3.6/site-packages/gensim/models/ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
/home/shayne/Anaconda3/envs/caps_env/lib/python3.6/site-packages/gensim/models/ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
/home/shayne/Anaconda3/envs/caps_env/lib/python3.6/site-packages/gensim/models/ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instea

/home/shayne/Anaconda3/envs/caps_env/lib/python3.6/site-packages/gensim/models/ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
/home/shayne/Anaconda3/envs/caps_env/lib/python3.6/site-packages/gensim/models/ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
/home/shayne/Anaconda3/envs/caps_env/lib/python3.6/site-packages/gensim/models/ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instea

/home/shayne/Anaconda3/envs/caps_env/lib/python3.6/site-packages/gensim/models/ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
/home/shayne/Anaconda3/envs/caps_env/lib/python3.6/site-packages/gensim/models/ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
/home/shayne/Anaconda3/envs/caps_env/lib/python3.6/site-packages/gensim/models/ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instea

In [ ]:
# LDA help vizualize
lda_display = pyLDAvis.gensim.prepare(lda_model, bow_corpus, dictionary)
pyLDAvis.display(lda_display)